# Cars: Getting Started

In [1]:
import numpy as np 
import pandas as pd 
import seaborn as sns 
import pyblp
sns.set_theme()
import matplotlib.pyplot as plt

pyblp.options.digits = 2
pyblp.options.verbose = False

# Read in data

The dataset, `cars.csv`, contains cleaned and processed data. If you want to make changes, the notebook, `materialize.ipynb`, creates the data from the raw source datsets. 

In [3]:
cars = pd.read_csv('cars.csv') # this reads the *balanced* dataset (i.e. J = 40 products per market always)
# cars = pd.read_excel('cars.xlsx') # this reads the *unbalanced* dataset (i.e. J varies over time)

### No data for France pre 1990. Average growth in adult fraction from other countries applied each year before

In [4]:
AdultFrac = pd.read_excel("FracOver20.xlsx", index_col = 0)
cars['adults'] = None
for idx in cars.index:
    cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]
cars

/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T/ipykernel_32700/1567250594.py:4: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]
/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/

ye  ma   co  zcode  brd                     type     brand    model  \
0     70   1   15     14    2             audi 100/200      audi  100/200   
1     70   1   26     35    4  citroen 2 CV 6 - 2 CV 4   citroen     2CV6   
2     70   1   36     36    4            citroen dyane   citroen    dyane   
3     70   1   64     67    7                 fiat 128      fiat      128   
4     70   1   71     80    8              ford escort      ford   escort   
...   ..  ..  ...    ...  ...                      ...       ...      ...   
5995  99   5  914    161   16               mercedes A  mercedes        A   
5996  99   5  936     80    8               ford focus      ford    focus   
5997  99   5  951    208   20              peugeot 206   peugeot      206   
5998  99   5  953    282   29           toyota avensis    toyota  avensis   
5999  99   5  978    287   29             toyota yaris    toyota    yaris   

      org  loc  ...    tax       pop           ngdp          rgdp  \
0       2    4  ...  0.250   9660000  1280999948288  3.940725e+12   
1       1    3  ...  0.250   9660000  1280999948288  3.940725e+12   
2       1    3  ...  0.250   9660000  1280999948288  3.940725e+12   
3       3    5  ...  0.250   9660000  1280999948288  3.940725e+12   
4       2    4  ...  0.250   9660000  1280999948288  3.940725e+12   
...   ...  ...  ...    ...       ...            ...           ...   
5995    2    4  ...  0.175  58200000   889870024704           NaN   
5996    7    4  ...  0.175  58200000   889870024704           NaN   
5997    1    3  ...  0.175  58200000   889870024704           NaN   
5998    4   12  ...  0.175  58200000   889870024704           NaN   
5999    4    6  ...  0.175  58200000   889870024704           NaN   

              engdp         ergdp        engdpc      ergdpc         inc  \
0       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
1       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
2       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
3       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
4       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
...             ...           ...           ...         ...         ...   
5995  1052244508672           NaN  18079.802734         NaN  32434.8905   
5996  1052244508672           NaN  18079.802734         NaN  32434.8905   
5997  1052244508672           NaN  18079.802734         NaN  32434.8905   
5998  1052244508672           NaN  18079.802734         NaN  32434.8905   
5999  1052244508672           NaN  18079.802734         NaN  32434.8905   

        adults  
0     0.688912  
1     0.688912  
2     0.688912  
3     0.688912  
4     0.688912  
...        ...  
5995  0.745551  
5996  0.745551  
5997  0.745551  
5998  0.745551  
5999  0.745551  

[6000 rows x 49 columns]

We estimate that 77% of the adult population have a driving license for a full-car. Hence, the share of population aged 20+ with a driver becomes:

In [7]:
license_share = 0.77
cars["ad_w_li"] = cars["adults"] * license_share 

In [4]:
lbl_vars = pd.read_csv('labels_variables.csv', index_col=0)
lbl_vals = pd.read_stata('cars.dta', iterator=True).value_labels() # the values that variables take (not relevant for all )

## Overview of the dataset

In [5]:
pd.set_option('display.max_colwidth', None)
tab = cars.mean(numeric_only=True).apply(lambda x: f'{x:.2f}').to_frame('Mean').join(lbl_vars)
tab

Mean  \
ye                   84.50   
ma                    3.00   
co                  207.50   
zcode               177.76   
brd                  16.79   
org                   2.72   
loc                   5.17   
cla                   2.30   
home                  0.32   
frm                  14.50   
qu                35606.68   
cy                 1337.09   
hp                   50.10   
we                  934.49   
pl                    4.88   
do                    3.55   
le                  409.24   
wi                  163.44   
he                  140.46   
li1                   6.59   
li2                   8.11   
li3                   8.92   
li                    7.87   
sp                  154.22   
ac                   16.27   
pr              2608988.58   
princ                 0.76   
eurpr              7256.92   
exppr            600384.65   
avexr               229.30   
avdexr              319.91   
avcpr               492.53   
avppr               671.77   
avdcpr               77.02   
avdppr               87.69   
xexr                 66.32   
tax                   0.21   
pop            49183800.00   
ngdp    178667304825541.97   
rgdp    216716720230172.44   
engdp      504371708122.45   
ergdp      659002565347.56   
engdpc            10015.84   
ergdpc            13264.84   
inc               26829.74   

                                                                                   label  
ye                                                      year (=first dimension of panel)  
ma                                                   market (=second dimension of panel)  
co                                                model code (=third dimension of panel)  
zcode               alternative model code (predecessors and successors get same number)  
brd                                                                           brand code  
org              origin code (demand side, country with which consumers associate model)  
loc                location code (production side, country where producer produce model)  
cla                                                                class or segment code  
home                          domestic car dummy (appropriate interaction of org and ma)  
frm                                                                            firm code  
qu                                               sales (number of new car registrations)  
cy                                               cylinder volume or displacement (in cc)  
hp                                                                    horsepower (in kW)  
we                                                                        weight (in kg)  
pl                                                places (number, not reliable variable)  
do                                                 doors (number, not reliable variable)  
le                                                                        length (in cm)  
wi                                                                         width (in cm)  
he                                                                        height (in cm)  
li1                             measure 1 for fuel efficiency (liter per km, at 90 km/h)  
li2                            measure 2 for fuel efficiency (liter per km, at 120 km/h)  
li3                          measure 3 for fuel efficiency (liter per km, at city speed)  
li                                             average of li1, li2, li3 (used in papers)  
sp                                                               maximum speed (km/hour)  
ac          time to acceleration (in seconds from 0 to 100 km/h, some from 0 to 96 km/h)  
pr                                      price (in destination currency including V.A.T.)  
princ   =pr/(ngdp/pop): price relative to per capita income (often used in demand model)  
eurpr   =pr/avdexr: price in common currency (in SDR times 1.2956 to interpret in Euros)  
ex

# Set up for analysis

## Price variables 

Can be either price (`pr`), price-to-income (`princ`), or log price (`logp`, created below).

In [6]:
price_var = 'eurpr'

In [7]:
cars['logp'] = np.log(cars[price_var])

## Market share

**Todo:** Decide how to measure the market size and thereby the market share. *Note:* Below is just an example that sets the market size = population / 3. 

In [8]:
# total quantity of cars sold in market-year (ma, ye)
cars['qu_tot'] = cars.groupby(['ma', 'ye'])['qu'].transform('sum')
cars['market_size'] = cars['pop'] * cars['adults']
cars['s'] = cars['qu'] / cars['market_size']

In [9]:
# compute the share of the outside good (will be useful for the demand inversion)
cars['s0'] = 1.0 - cars.groupby(['ma', 'ye'])['s'].transform('sum')
print(f'Outside share is from {cars.s0.min():.1%} to {cars.s0.max():.1%}')

Outside share is from 94.4% to 97.8%


In [10]:
cars.groupby(['ma'])['s'].describe().rename(index=lbl_vals['market']).style.format('{:.3f}')

## 1. Using canned software

In [11]:
from linearmodels.iv import IV2SLS

In [12]:
cars['delta'] = cars['s'] / cars['s0']
cars['delta'] = np.log(cars['delta'].values.astype(float)) ## Den stoppede med at ville gøre det i et skridt uden at definere type

In [13]:
cars["brand"].replace('alfa romeo', 'alfa_romeo', inplace=True)
cars["brand"] = cars["brand"].str.replace('/', '', regex=False)

In [14]:
categorical_var = 'brand' # name of categorical variable
dummies = pd.get_dummies(cars[categorical_var]) # creates a matrix of dummies for each value of dummyvar
x_vars_dummies = list(dummies.columns[1:].values) # omit a reference category, here it is the first (hence columns[1:])

# add dummies to the dataframe 
assert dummies.columns[0] not in cars.columns, f'It looks like you have already added this dummy to the dataframe. Avoid duplicates! '
cars = pd.concat([cars,dummies], axis=1)

In [15]:
# choose your preferred variables 
x_vars = ['logp', 'home', 'cy', 'hp', 'we', 'li', 'sp'] + x_vars_dummies # <--- !!! CHOOSE HERE 
print(x_vars)

['logp', 'home', 'cy', 'hp', 'we', 'li', 'sp', 'MCC', 'VW', 'alfa_romeo', 'audi', 'citroen', 'daewoo', 'daf', 'fiat', 'ford', 'honda', 'hyundai', 'innocenti', 'lancia', 'mazda', 'mercedes', 'mitsubishi', 'nissan', 'opel', 'peugeot', 'renault', 'rover', 'saab', 'seat', 'skoda', 'suzuki', 'talbot', 'talhillman', 'talmatra', 'talsimca', 'talsunb', 'toyota', 'volvo']


In [16]:
formula = 'delta ~ 1'
for x_ in x_vars:
    formula += ' + ' + x_
print(formula)
model = IV2SLS.from_formula(formula, cars).fit()

delta ~ 1 + logp + home + cy + hp + we + li + sp + MCC + VW + alfa_romeo + audi + citroen + daewoo + daf + fiat + ford + honda + hyundai + innocenti + lancia + mazda + mercedes + mitsubishi + nissan + opel + peugeot + renault + rover + saab + seat + skoda + suzuki + talbot + talhillman + talmatra + talsimca + talsunb + toyota + volvo


c:\Users\PSand\anaconda3\lib\site-packages\linearmodels\iv\model.py:557: MissingValueWarning: 
Inputs contain missing values. Dropping rows with missing observations.
  super().__init__(


In [17]:
model.summary

<class 'linearmodels.compat.statsmodels.Summary'>
"""
                            OLS Estimation Summary                            
==============================================================================
Dep. Variable:                  delta   R-squared:                      0.4004
Estimator:                        OLS   Adj. R-squared:                 0.3965
No. Observations:                5998   F-statistic:                 1.484e+05
Date:                Fri, Oct 18 2024   P-value (F-stat)                0.0000
Time:                        01:56:43   Distribution:                 chi2(39)
Cov. Estimator:                robust                                         
                                                                              
                             Parameter Estimates                              
==============================================================================
            Parameter  Std. Err.     T-stat    P-value    Lower CI    Upper CI
------------------------------------------------------------------------------
Intercept     -9.0530     0.2558    -35.385     0.0000     -9.5545     -8.5516
logp           0.0318     0.0366     0.8677     0.3856     -0.0400      0.1035
home           1.0375     0.0233     44.466     0.0000      0.9917      1.0832
cy            -0.0003  7.261e-05    -3.6543     0.0003     -0.0004     -0.0001
hp            -0.0323     0.0022    -14.784     0.0000     -0.0365     -0.0280
we             0.0005     0.0001     3.7499     0.0002      0.0003      0.0008
li            -0.0270     0.0114    -2.3794     0.0173     -0.0493     -0.0048
sp             0.0193     0.0017     11.265     0.0000      0.0160      0.0227
MCC           -1.0477     0.1166    -8.9815     0.0000     -1.2763     -0.8190
VW             0.0936     0.0580     1.6125     0.1068     -0.0202      0.2073
alfa_romeo    -0.5303     0.0658    -8.0612     0.0000     -0.6592     -0.4013
audi          -0.1522     0.0587    -2.5914     0.0096     -0.2673     -0.0371
citroen       -0.3786     0.0537    -7.0438     0.0000     -0.4839     -0.2732
daewoo        -0.5210     0.1577    -3.3040     0.0010     -0.8301     -0.2119
daf           -0.7373     0.1584    -4.6552     0.0000     -1.0477     -0.4269
fiat          -0.1954     0.0518    -3.7721     0.0002     -0.2969     -0.0939
ford           0.1666     0.0511     3.2615     0.0011      0.0665      0.2668
honda         -0.2393     0.0748    -3.1974     0.0014     -0.3860     -0.0926
hyundai       -0.7528     0.1328    -5.6666     0.0000     -1.0131     -0.4924
innocenti     -1.1869     0.2144    -5.5371     0.0000     -1.6071     -0.7668
lancia        -0.8377     0.0759    -11.032     0.0000     -0.9865     -0.6888
mazda         -0.1598     0.0650    -2.4581     0.0140     -0.2873     -0.0324
mercedes       0.3787     0.0608     6.2259     0.0000      0.2594      0.4979
mitsubishi    -0.2161     0.0742    -2.9107     0.0036     -0.3616     -0.0706
nissan        -0.1659     0.0526    -3.1540     0.0016     -0.2691     -0.0628
opel           0.0252     0.0554     0.4540     0.6498     -0.0835      0.1338
peugeot       -0.1194     0.0555    -2.1528     0.0313     -0.2281     -0.0107
renault       -0.0131     0.0502    -0.2609     0.7942     -0.1115      0.0853
rover         -0.4312     0.0578    -7.4619     0.0000     -0.5444     -0.3179
saab          -0.8923     0.1505    -5.9310     0.0000     -1.1872     -0.5974
seat          -0.6337     0.0668    -9.4798     0.0000     -0.7647     -0.5027
skoda         -0.7790     0.0956    -8.1448     0.0000     -0.9665     -0.5916
suzuki        -0.7103     0.0880    -8.0753     0.0000     -0.8827     -0.5379
talbot        -0.4234     0.0789    -5.3632     0.0000     -0.5781     -0.2687
talhillman    -1.0857     0.2123    -5.1139     0.0000     -1.5019     -0.6696
talmatra      -2.7319     0.0761    -35.891     0.0000     -2.8811     -2.5828
talsimca      -0.3245     0.1055    -3.0766     0.0021     -0.5313     -0.1

In [19]:
K = len(x_vars)
N = cars.ma.nunique() * cars.ye.nunique()
J = 40 
x = cars[x_vars].values.reshape((N,J,K)).astype(float)
cars['outcome'] = cars['s'] / cars['s0']
y = cars['delta'].values.reshape((N,J))
# standardize x
x = ((x - x.mean(0).mean(0))/(x.std(0).std(0)))

# Towards non-linear estimation

In order to work with the logit model, you have to be able to compute the utility indices, which typically take the form of some inner product of an $x$-vector and a $\theta$ vector. This is illustrated for you below. Since `x` is `(N,J,K)` (i.e. `x[i,j,:]` gives the $K$-vector of regressors for the car `j` in market-period `i`), we just have to form the matrix product `x @ theta`, and Python will do the sum over the 3rd dimension of `x`. 

In [ ]:
theta0 = np.zeros((K,))
v = x @ theta0 # how to multiply a trial value with the matrix of regressors 
np.exp(v) / np.sum(np.exp(v), 1, keepdims=True) # choice probabilities 